In [39]:
# Imports de librerias de preprocesamiento de texto
import re, string, unicodedata
import nltk
import contractions
import inflect
from bs4 import BeautifulSoup
from nltk import word_tokenize, sent_tokenize
from nltk.corpus import stopwords
from nltk.stem import LancasterStemmer, WordNetLemmatizer

import pandas as pd
import numpy as np

#libreria de geolocalizacion
import geocoder

In [94]:
data = pd.read_csv("../data/train.csv", index_col="id", parse_dates=["fecha"]).reset_index()
data["tipodepropiedad"] = data["tipodepropiedad"].map(lambda x: str(x).lower())

In [32]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 240000 entries, 0 to 239999
Data columns (total 23 columns):
id                            240000 non-null int64
titulo                        234613 non-null object
descripcion                   240000 non-null object
tipodepropiedad               240000 non-null object
direccion                     186928 non-null object
ciudad                        239628 non-null object
provincia                     239845 non-null object
antiguedad                    196445 non-null float64
habitaciones                  217529 non-null float64
garages                       202235 non-null float64
banos                         213779 non-null float64
metroscubiertos               222600 non-null float64
metrostotales                 188533 non-null float64
idzona                        211379 non-null float64
lat                           116512 non-null float64
lng                           116512 non-null float64
fecha                         240

# Limpieza de descripciones

In [95]:
def apply_batery_functions(text):
    text = strip_html(text)
    text = remove_between_square_brackets(text)
    text = denoise_text(text)
    return replace_contractions(text)
    
def strip_html(text):
    soup = BeautifulSoup(text, "html.parser")
    return soup.get_text()

def remove_between_square_brackets(text):
    return re.sub('\[[^]]*\]', '', text)

def denoise_text(text):
    text = strip_html(text)
    text = remove_between_square_brackets(text)
    return text

def replace_contractions(text):
    """Replace contractions in string of text"""
    return contractions.fix(text)

In [96]:
data["descripcion"].fillna(value="",inplace=True)

In [97]:
data.loc[:, "descripcion"] = data.descripcion.apply(lambda x: strip_html(x))

/usr/local/lib/python3.7/site-packages/bs4/__init__.py:294: UserWarning: "b'.'" looks like a filename, not markup. You should probably open this file and pass the filehandle into Beautiful Soup.
  ' Beautiful Soup.' % markup)
/usr/local/lib/python3.7/site-packages/bs4/__init__.py:294: UserWarning: "b'/'" looks like a filename, not markup. You should probably open this file and pass the filehandle into Beautiful Soup.
  ' Beautiful Soup.' % markup)


# Analizo la validez de los que hay

In [98]:
notMissing = data[data["direccion"].notnull()]

In [99]:
notMissing = notMissing.dropna(subset=['ciudad', 'provincia'])

In [100]:
notMissing.shape[0]

186787

In [9]:
notMissing.head()

id                                             titulo  \
0  254099                                  depto. tipo a-402   
1   53461                     condominio horizontal en venta   
2  247984              casa en venta urbi 3 recamaras tonala   
3  209067  casa sola en toluca zinacantepec con credito i...   
4  185997                                     paseos del sol   

                                         descripcion     tipodepropiedad  \
0  depto. interior de 80.15m2, consta de sala com...         apartamento   
1  entre sonora y guerrero, atrás del hospital án...  casa en condominio   
2  descripcion \nla mejor ubicacion residencial e...                casa   
3  casa en privada con caseta de vigilancia casas...                casa   
4  bonito departamento en excelentes condiciones ...         apartamento   

                         direccion                  ciudad         provincia  \
0  Avenida Division del Norte 2005           Benito Juárez  Distrito Federal   
1                       AV. MEXICO  La Magdalena Contreras  Distrito Federal   
2                      Urbi Tonala                  Tonalá           Jalisco   
3    IGNACIO MANUEL ALTAMIRANO 128            Zinacantepec    Edo. de México   
4                  PASEOS DEL SOL                  Zapopan           Jalisco   

   antiguedad  habitaciones  garages  ...   idzona        lat        lng  \
0         NaN           2.0      1.0  ...  23533.0        NaN        NaN   
1        10.0           3.0      2.0  ...  24514.0  19.310205 -99.227655   
2         5.0           3.0      2.0  ...  48551.0        NaN        NaN   
3         1.0           2.0      1.0  ...  53666.0  19.301890 -99.688015   
4        10.0           2.0      1.0  ...  47835.0        NaN        NaN   

       fecha  gimnasio  usosmultiples piscina  escuelascercanas  \
0 2015-08-23       0.0            0.0     0.0               0.0   
1 2013-06-28       0.0            0.0     0.0               1.0   
2 2015-10-17       0.0            0.0     0.0               0.0   
3 2012-03-09       0.0            0.0     0.0               1.0   
4 2016-06-07       0.0            0.0     0.0               0.0   

   centroscomercialescercanos     precio  
0                         0.0  2273000.0  
1                         1.0  3600000.0  
2                         0.0  1200000.0  
3                         1.0   650000.0  
4                         0.0  1150000.0  

[5 rows x 23 columns]

In [8]:
def getFormatForRequest(direccion, ciudad):
    direccionTokens = direccion.split()
    ciudadTokens = ciudad.split()
    separator = "+"
    s1 = separator.join(direccionTokens)
    s1 = s1 + ","
    s2 = separator.join(ciudadTokens)
    return s1 + s2 + ",+MX"

In [9]:
import requests

baseUrl = "http://www.datasciencetoolkit.org/maps/api/geocode/json?sensor=false&address="

### El formato deberia ser baseUrl + address=+direccion,+ciudad,+MX
#donde ciudad y direccion tienen que ser tokenizados por el mas

r = requests.get(baseUrl + notMissing["direccion"][0] + notMissing["ciudad"][0])

In [29]:
r.json()

{'status': 'OK',
 'results': [{'address_components': [{'long_name': 'Ciudad Juárez, MX',
     'types': ['locality', 'political'],
     'short_name': 'Ciudad Juárez'},
    {'long_name': 'Mexico',
     'types': ['country', 'political'],
     'short_name': 'MX'}],
   'geometry': {'location_type': 'APPROXIMATE',
    'viewport': {'southwest': {'lat': 31.589548111, 'lng': -106.592124939},
     'northeast': {'lat': 31.7833595276, 'lng': -106.315124512}},
    'location': {'lat': 31.73333, 'lng': -106.48333}},
   'types': ['locality', 'political']}]}

In [10]:
import json
from pandas.io.json import json_normalize

In [11]:
import glob,os

path =r'/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks'
allFiles = glob.glob(path + "/*.csv")
frame = pd.DataFrame()
list_ = []
for file_ in allFiles:
    print (file_)
    df = pd.read_csv(file_,low_memory=False)
    list_.append(df)
frame = pd.concat(list_)
frame.drop_duplicates(["notMissingId"],inplace=True)
frame.to_csv('/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/mergeCoords.csv',sep=",",index=False)

/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords4.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords5.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords7.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords6.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords2.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords3.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords1.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords20.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords21.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords19.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords18.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords15.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords14.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords16.csv
/Users/llopezlecube/Datos/7506_2c2019_tp1/notebooks/coords17.csv
/Users/llopezlecube/Datos/7506_2

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:11: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  # This is added back by InteractiveShellApp.init_path()


In [13]:
jsonDataframeSaved = pd.read_csv("mergeCoords.csv").sort_values(by='notMissingId')

In [ ]:
jsonDataframeSaved["notMissingId"] = jsonDataframeSaved["notMissingId"].astype(int)

In [16]:
jsonDataframeSaved.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10809 entries, 7980 to 10808
Data columns (total 12 columns):
Unnamed: 0                         10809 non-null int64
address_components                 10809 non-null object
formatted_address                  3 non-null object
geometry.location.lat              10809 non-null float64
geometry.location.lng              10809 non-null float64
geometry.location_type             10809 non-null object
geometry.viewport.northeast.lat    10291 non-null float64
geometry.viewport.northeast.lng    10291 non-null float64
geometry.viewport.southwest.lat    10291 non-null float64
geometry.viewport.southwest.lng    10291 non-null float64
notMissingId                       10809 non-null int64
types                              10809 non-null object
dtypes: float64(6), int64(2), object(4)
memory usage: 1.1+ MB


In [17]:
indices = notMissing.index.tolist()
visitIndex = jsonDataframeSaved["notMissingId"].tolist()
for i in visitIndex:
    try:
        indices.remove(i)
    except:
        print("Fail with id",i)
for i in indices:
    if i <= sorted(jsonDataframeSaved["notMissingId"].tolist(), reverse=True)[0]:
        indices.remove(i)

In [18]:
len(indices)

167448

In [139]:
indices = notMissing.index.tolist()
jsonDataframe["notMissingId"] = jsonDataframe["notMissingId"].astype(int)
visitIndex = jsonDataframe["notMissingId"].tolist()
for i in visitIndex:
    try:
        indices.remove(i)
    except:
        print("Fail with id",i)
    
lastIndex = sorted(jsonDataframe["notMissingId"].tolist(), reverse=True)[0]   
for i in indices:
    if i <= lastIndex:
        indices.remove(i)

Fail with id 16516
Fail with id 16518
Fail with id 16525
Fail with id 16529
Fail with id 16533
Fail with id 16546
Fail with id 16557
Fail with id 16561
Fail with id 16563
Fail with id 16564
Fail with id 16565
Fail with id 16569
Fail with id 16573
Fail with id 16576
Fail with id 16579
Fail with id 16583
Fail with id 16584
Fail with id 16597
Fail with id 16599
Fail with id 16601
Fail with id 16602
Fail with id 16609
Fail with id 16612
Fail with id 16614
Fail with id 16620
Fail with id 16621
Fail with id 16625
Fail with id 16633
Fail with id 16634
Fail with id 16636
Fail with id 16641
Fail with id 16646
Fail with id 16647
Fail with id 16648
Fail with id 16649
Fail with id 16650
Fail with id 16658
Fail with id 16666
Fail with id 16670
Fail with id 16672
Fail with id 16679
Fail with id 16681
Fail with id 16682
Fail with id 16689
Fail with id 16690
Fail with id 16702
Fail with id 16703
Fail with id 16704
Fail with id 16710
Fail with id 16711
Fail with id 16713
Fail with id 16714
Fail with id

In [140]:
len(indices)

176208

In [19]:
jsonDataframe = json_normalize(json.loads(json.dumps(r.json()))['results'])

In [20]:
jsonDataframe.drop(jsonDataframe.index, inplace=True)

In [71]:
#jsonDataframe["notMissingIndexId"] = pd.Series(notMissing.index.tolist())

In [72]:
jsonDataframe.head()

address_components  geometry.location.lat  \
0  [{'types': ['locality', 'political'], 'long_na...               31.73333   
1  [{'types': ['locality', 'political'], 'long_na...               19.44506   
2  [{'types': ['administrative_area_level_1', 'po...               40.50670   
3  [{'types': ['locality', 'political'], 'long_na...               19.64388   
4  [{'types': ['administrative_area_level_1', 'po...               20.50000   

   geometry.location.lng geometry.location_type  \
0             -106.48333            APPROXIMATE   
1              -99.14612            APPROXIMATE   
2               35.91330            APPROXIMATE   
3              -99.21598            APPROXIMATE   
4              -99.00000            APPROXIMATE   

  geometry.viewport.northeast.lat geometry.viewport.northeast.lng  \
0                         31.7834                        -106.315   
1                         19.5831                        -98.9296   
2                         41.5067                         36.9133   
3                         19.7202                        -99.1652   
4                         21.1793                        -98.1398   

  geometry.viewport.southwest.lat geometry.viewport.southwest.lng  \
0                         31.5895                        -106.592   
1                         19.1389                        -99.3579   
2                         39.5067                         34.9133   
3                         19.5796                        -99.2828   
4                         19.5849                        -99.8498   

                                      types  notMissingId  
0                     [locality, political]       16516.0  
1                     [locality, political]       16518.0  
2  [administrative_area_level_1, political]       16525.0  
3                     [locality, political]       16529.0  
4  [administrative_area_level_1, political]       16533.0

In [60]:
notMissing["ciudad"].isnull().value_counts()

False    186787
True        141
Name: ciudad, dtype: int64

In [61]:
missingCity = notMissing[notMissing["ciudad"].isnull()]

In [22]:
visitsIndex = []
count = 0
for i in notMissing.index:
    if (count % 10 == 0):
         print(count, end = "---")
    try:
        requestJson = requests.get(baseUrl + notMissing["direccion"][i] + notMissing["ciudad"][i]).json()
        toUpdate = json_normalize(json.loads(json.dumps(requestJson))['results'])
        toUpdate["notMissingId"] = i
        jsonDataframe = pd.concat([jsonDataframe, toUpdate], join= 'outer', sort=False, ignore_index=True)
    except KeyError:
        requestJson = requests.get(baseUrl + notMissing["direccion"][i] + notMissing["provincia"][i]).json()
        toUpdate = json_normalize(json.loads(json.dumps(requestJson))['results'])
        toUpdate["notMissingId"] = i
        jsonDataframe = pd.concat([jsonDataframe, toUpdate], join= 'outer', sort=False, ignore_index=True)
    visitsIndex.append(i)
    count += 1 

0---10---20---30---40---50---60---70---80---90---100---110---120---130---140---150---160---170---180---190---200---210---220---230---240---250---260---270---280---290---300---310---320---330---340---350---360---370---380---390---400---410---420---430---440---450---460---470---480---490---500---510---520---530---540---550---560---570---580---590---600---610---620---630---640---650---660---670---680---690---700---710---720---730---740---750---760---770---780---790---800---810---820---830---840---850---860---870---880---890---900---910---920---930---940---950---960---970---980---990---1000---1010---1020---1030---1040---1050---1060---1070---1080---1090---1100---1110---1120---1130---1140---1150---1160---1170---1180---1190---1200---1210---1220---1230---1240---1250---1260---1270---1280---1290---1300---1310---1320---1330---1340---1350---1360---1370---1380---1390---1400---1410---1420---1430---1440---1450---1460---1470---1480---1490---1500---1510---1520---1530---1540---1550---1560---1570---1580-

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [ ]:
count = 0
for i in indices:
    if(i not in visitIndex):
        if (count % 10 == 0):
            print(count, end = "---")
        try:
            requestJson = requests.get(baseUrl + notMissing["direccion"][i] + notMissing["ciudad"][i]).json()
            toUpdate = json_normalize(json.loads(json.dumps(requestJson))['results'])
            toUpdate["notMissingId"] = i
            jsonDataframe = pd.concat([jsonDataframe, toUpdate], join= 'outer', sort=False, ignore_index=True)
        except KeyError:
            requestJson = requests.get(baseUrl + notMissing["direccion"][i] + notMissing["provincia"][i]).json()
            toUpdate = json_normalize(json.loads(json.dumps(requestJson))['results'])
            toUpdate["notMissingId"] = i
            jsonDataframe = pd.concat([jsonDataframe, toUpdate], join= 'outer', sort=False, ignore_index=True)
        visitIndex.append(i)
        count += 1 

0---10---20---30---40---50---60---70---80---90---100---110---120---130---140---150---160---170---180---190---200---

In [100]:
jsonDataframe.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 65554 entries, 0 to 65553
Data columns (total 11 columns):
address_components                 65554 non-null object
geometry.location.lat              65554 non-null float64
geometry.location.lng              65554 non-null float64
geometry.location_type             65554 non-null object
geometry.viewport.northeast.lat    62314 non-null object
geometry.viewport.northeast.lng    62314 non-null object
geometry.viewport.southwest.lat    62314 non-null object
geometry.viewport.southwest.lng    62314 non-null object
types                              65554 non-null object
notMissingId                       65554 non-null float64
formatted_address                  16 non-null object
dtypes: float64(3), object(8)
memory usage: 5.5+ MB


In [96]:
jsonDataframe.to_csv("coords38.csv")

In [54]:
getFormatForRequest(notMissing["direccion"][12554],notMissing["ciudad"][12554])

'Calle+16+de+septiembre+Colonia+Llano+Grande+Metepec,Metepec,+MX'

In [157]:
jsonDataframe.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 830 entries, 0 to 829
Data columns (total 10 columns):
address_components                 830 non-null object
geometry.location.lat              830 non-null float64
geometry.location.lng              830 non-null float64
geometry.location_type             830 non-null object
geometry.viewport.northeast.lat    779 non-null object
geometry.viewport.northeast.lng    779 non-null object
geometry.viewport.southwest.lat    779 non-null object
geometry.viewport.southwest.lng    779 non-null object
types                              830 non-null object
notMissingId                       830 non-null float64
dtypes: float64(3), object(7)
memory usage: 64.9+ KB


In [295]:
notMissing.loc[57591]

id                                                                        10884
titulo                                      departamento en venta en cuauhtemoc
descripcion                   nocnok id: mx16-cg8006. ¿aun pagas renta?  ¿tu...
tipodepropiedad                                                     apartamento
direccion                                                        Mezquital  #32
ciudad                                                               Cuauhtémoc
provincia                                                      Distrito Federal
antiguedad                                                                  NaN
habitaciones                                                                  2
garages                                                                       1
banos                                                                         1
metroscubiertos                                                              60
metrostotales                           

In [296]:
jsons[57591]

{'results': [{'address_components': [{'types': ['locality', 'political'],
     'short_name': 'Mezquital del Oro',
     'long_name': 'Mezquital del Oro, MX'},
    {'types': ['country', 'political'],
     'short_name': 'MX',
     'long_name': 'Mexico'}],
   'geometry': {'viewport': {'southwest': {'lng': -103.36859068084,
      'lat': 21.2061111681218},
     'northeast': {'lng': -103.357804123317, 'lat': 21.2230446377094}},
    'location': {'lng': -103.38333, 'lat': 21.16667},
    'location_type': 'APPROXIMATE'},
   'types': ['locality', 'political']}],
 'status': 'OK'}

In [109]:
indices = notMissing.index.tolist()
for i in visitsIndex:
    indices.remove(i)

In [110]:
len(indices)

173946

# Analizo los faltantes

In [8]:
missings = data[data["direccion"].isnull()]

In [10]:
missings.shape

(53072, 23)

In [13]:
missings["descripcion"].map(lambda x: print(x + "\n" + ".-.-.-.-.-.-.-.-.-.-.-.-.-.-.-." + "\n") )

ubicada en esquina, pertenece san lorenzo agencia santiago etla.
cuenta con:
tres recamaras
2 baños completos
sala
comedor- cocina
cisterna
fosa séptica
patio. easybroker id: eb-t3055
.-.-.-.-.-.-.-.-.-.-.-.-.-.-.-.

departamento nuevo ,256 m2 de construccion,un departamento por piso,acabados de lujo,elevador directo a tu departamento,elevador de servicio,cocina integral ,lavavajillas, ,boliler,clinas con 5 aparatos, ilumimacion natural ,espejos ,,1 bodegas,dos cajones de estacinamiento ,vista panoramica,amenidades alberca,jacuzzi,salon   de eventos,ginmasio,sala de juntas, vigilancia 24 hrs ,camara de seguridad $7;
.-.-.-.-.-.-.-.-.-.-.-.-.-.-.-.

pre venta de residencia en la toscana con excelente distribución, cuenta con vestidor y baño todas las recamaras.
.-.-.-.-.-.-.-.-.-.-.-.-.-.-.-.

casa en dos niveles, 3 recámaras la principal con baño, sala, comedor con pisos laminados, cocina equipada con alacena, cuarto de servicio, 4 baños completos, centro de lavado, bodega, terraza, ja

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



terreno al norte de la ciudad en la delegación gustavo a. madero, excelente para desarrollo pequeño, zona con buenas vías de comunicación a unos metros de la estación del metro martín carrera.   terreno al norte de la ciudad en la delegación gustavo a. madero. excelente para desarrollo pequeño, zona con buenas vías de comunicación a unos metros de la estación del metro martín carrera.
.-.-.-.-.-.-.-.-.-.-.-.-.-.-.-.

casa de 2 plantas con 3 recamaras, 2 baños y medio, cocina integral nueva, estufa, boiler, despensa , lavandería cerrada, protectores en toda las ventanas, patio, cochera sin techar para un carro, cerca del parque .cnrcv-9340
.-.-.-.-.-.-.-.-.-.-.-.-.-.-.-.

terreno campestre de forma rectangular de 16 de frente por 20 de fondo, muy cercano del camino a santa rita, cuenta con instalaciones para agua, drenaje y electricidad. bardeado
.-.-.-.-.-.-.-.-.-.-.-.-.-.-.-.

bonita y comoda casa en san agustin tlaxiaca. proyecto de una privada con 10 casas con pequeña área común con

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



# Analizo los resultados de los requests

In [64]:
pd.options.mode.chained_assignment = None

In [114]:
requests = pd.read_csv("mergeCoords.csv")

/usr/local/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3049: DtypeWarning: Columns (5,6,7,9,30,31,32) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [115]:
requests.drop(columns=["antiguedad", "banos", "centroscomercialescercanos", "ciudad", "descripcion", \
                      "direccion", "escuelascercanas", "fecha", "formatted_address", "garages",\
                      "gimnasio", "habitaciones", "id", "idzona","lat", "lng", "metroscubiertos", \
                       "metrostotales", "piscina", "provincia", "tipodepropiedad", "titulo", \
                      "types", "usosmultiples","precio", "Unnamed: 0"], inplace=True)
requests.rename(columns={"notMissingId":"innerId"}, inplace=True)
requests["innerId"].dropna(inplace=True)
requests["innerId"] = requests["innerId"].astype("Int64")

In [116]:
requests.dtypes

address_components                  object
geometry.location.lat              float64
geometry.location.lng              float64
geometry.location_type              object
geometry.viewport.northeast.lat    float64
geometry.viewport.northeast.lng    float64
geometry.viewport.southwest.lat    float64
geometry.viewport.southwest.lng    float64
innerId                              Int64
dtype: object

In [117]:
requests.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 72429 entries, 0 to 72428
Data columns (total 9 columns):
address_components                 72428 non-null object
geometry.location.lat              72428 non-null float64
geometry.location.lng              72428 non-null float64
geometry.location_type             72428 non-null object
geometry.viewport.northeast.lat    68835 non-null float64
geometry.viewport.northeast.lng    68835 non-null float64
geometry.viewport.southwest.lat    68835 non-null float64
geometry.viewport.southwest.lng    68835 non-null float64
innerId                            72428 non-null Int64
dtypes: Int64(1), float64(6), object(2)
memory usage: 5.0+ MB


In [92]:
requests.sort_values(by=["innerId"])

Unnamed: 0                                 address_components  \
7980            0  [{'types': ['locality', 'political'], 'short_n...   
4576            0  [{'types': ['locality', 'political'], 'long_na...   
1795            0  [{'types': ['locality', 'political'], 'long_na...   
1796            1  [{'types': ['locality', 'political'], 'long_na...   
4577            1  [{'types': ['locality', 'political'], 'long_na...   
4578            2  [{'types': ['locality', 'political'], 'long_na...   
4579            3  [{'types': ['locality', 'political'], 'long_na...   
7981            7  [{'types': ['locality', 'political'], 'short_n...   
7982            8  [{'types': ['administrative_area_level_1', 'po...   
4580            4  [{'types': ['locality', 'political'], 'long_na...   
4581            5  [{'types': ['locality', 'political'], 'long_na...   
7983           11  [{'types': ['locality', 'political'], 'short_n...   
4582            6  [{'types': ['locality', 'political'], 'long_na...   
4583            7  [{'types': ['locality', 'political'], 'long_na...   
4584            8  [{'types': ['locality', 'political'], 'long_na...   
1797            2  [{'types': ['locality', 'political'], 'long_na...   
7984           16  [{'types': ['locality', 'political'], 'short_n...   
4585            9  [{'types': ['administrative_area_level_1', 'po...   
7985           18  [{'types': ['locality', 'political'], 'short_n...   
7986           19  [{'types': ['locality', 'political'], 'short_n...   
7987           20  [{'types': ['locality', 'political'], 'short_n...   
1798            3  [{'types': ['locality', 'political'], 'long_na...   
4586           10  [{'types': ['locality', 'political'], 'long_na...   
4587           11  [{'types': ['locality', 'political'], 'long_na...   
1799            4  [{'types': ['locality', 'political'], 'long_na...   
7988           25  [{'types': ['locality', 'political'], 'short_n...   
7989           26  [{'types': ['administrative_area_level_1', 'po...   
7990           27  [{'types': ['locality', 'political'], 'short_n...   
7991           28  [{'types': ['administrative_area_level_1', 'po...   
1800            5  [{'types': ['locality', 'political'], 'long_na...   
...           ...                                                ...   
72399       66665  [{'long_name': 'Ecatepec, MX', 'types': ['loca...   
72400       66666  [{'long_name': 'Col', 'types': ['administrativ...   
72401       66667  [{'long_name': 'Cholula, MX', 'types': ['local...   
72402       66668  [{'long_name': 'La Reforma, MX', 'types': ['lo...   
72403       66669  [{'long_name': 'Naucalpan de Juárez, MX', 'typ...   
72404       66670  [{'long_name': 'Morelia, MX', 'types': ['local...   
72405       66671  [{'long_name': 'Tyre, LB', 'types': ['locality...   
72406       66672  [{'long_name': 'Cancún, MX', 'types': ['locali...   
72407       66673  [{'long_name': 'Ciudad Juárez, MX', 'types': [...   
72408       66674  [{'long_name': 'Coyoacán, MX', 'types': ['loca...   
72409       66675  [{'long_name': 'Ciudad Juárez, MX', 'types': [...   
72410       66676  [{'long_name': 'Tepehua, MX', 'types': ['local...   
72411       66677  [{'long_name': 'Estado de Hidalgo, MX', 'types...   
72412       66678  [{'long_name': 'Juan', 'types': ['locality', '...   
72413       66679  [{'long_name': 'La', 'types': ['administrative...   
72414       66680  [{'long_name': 'Arias, IT', 'types': ['localit...   
72415       66681  [{'long_name': 'Coyoacán, MX', 'types': ['loca...   
72416       66682  [{'long_name': None, 'types': ['country', 'pol...   
72417       66683  [{'long_name': 'Col', 'types': ['administrativ...   
72418       66684  [{'long_name': 'Ciudad Juárez, MX', 'types': [...   
72419       66685  [{'long_name': 'Az', 'types': ['administrative...   
72420       66686  [{'long_name': 'Ciudad Juárez, MX', 'types': [...   
72421       66687  [{'long_name': 'Ciudad Juárez, MX', 'types': [...   
72422       66688  [{'long_name': 'Estado de Hi

In [105]:
notMissing["innerId"] = pd.Series(notMissing.index.tolist())
notMissing["innerId"] = notMissing["innerId"].astype("Int64")

In [122]:
notMissing.dtypes

id                                     int64
titulo                                object
descripcion                           object
tipodepropiedad                       object
direccion                             object
ciudad                                object
provincia                             object
antiguedad                           float64
habitaciones                         float64
garages                              float64
banos                                float64
metroscubiertos                      float64
metrostotales                        float64
idzona                               float64
lat                                  float64
lng                                  float64
fecha                         datetime64[ns]
gimnasio                             float64
usosmultiples                        float64
piscina                              float64
escuelascercanas                     float64
centroscomercialescercanos           float64
precio    

In [118]:
inner_join = requests.merge(notMissing,how="inner",on="innerId")

In [125]:
inner_join[(inner_join["geometry.location.lat"].notnull() & inner_join["geometry.location.lng"].notnull()) & \
          (inner_join["lat"].isnull() & inner_join["lng"].isnull())]

address_components  \
0      [{'types': ['locality', 'political'], 'long_na...   
1      [{'types': ['administrative_area_level_1', 'po...   
2      [{'types': ['locality', 'political'], 'long_na...   
4      [{'types': ['locality', 'political'], 'long_na...   
5      [{'types': ['locality', 'political'], 'long_na...   
6      [{'types': ['locality', 'political'], 'long_na...   
7      [{'types': ['locality', 'political'], 'long_na...   
8      [{'types': ['locality', 'political'], 'long_na...   
10     [{'types': ['locality', 'political'], 'long_na...   
11     [{'types': ['locality', 'political'], 'long_na...   
13     [{'types': ['locality', 'political'], 'long_na...   
15     [{'types': ['administrative_area_level_1', 'po...   
17     [{'types': ['locality', 'political'], 'long_na...   
18     [{'types': ['locality', 'political'], 'long_na...   
19     [{'types': ['locality', 'political'], 'long_na...   
20     [{'types': ['locality', 'political'], 'long_na...   
21     [{'types': ['locality', 'political'], 'long_na...   
23     [{'types': ['locality', 'political'], 'long_na...   
28     [{'types': ['locality', 'political'], 'long_na...   
29     [{'types': ['locality', 'political'], 'long_na...   
32     [{'types': ['locality', 'political'], 'long_na...   
33     [{'types': ['locality', 'political'], 'long_na...   
34     [{'types': ['administrative_area_level_1', 'po...   
35     [{'types': ['locality', 'political'], 'long_na...   
36     [{'types': ['locality', 'political'], 'long_na...   
39     [{'types': ['locality', 'political'], 'long_na...   
40     [{'types': ['locality', 'political'], 'long_na...   
43     [{'types': ['locality', 'political'], 'long_na...   
44     [{'types': ['locality', 'political'], 'long_na...   
45     [{'types': ['administrative_area_level_1', 'po...   
...                                                  ...   
56304  [{'long_name': 'La', 'types': ['administrative...   
56305  [{'long_name': 'Estado de Hidalgo, MX', 'types...   
56306  [{'long_name': 'Estado de Hidalgo, MX', 'types...   
56308  [{'long_name': 'El Valle Real, DO', 'types': [...   
56309  [{'long_name': 'Iztapalapa, MX', 'types': ['lo...   
56310  [{'long_name': 'Ciudad Juárez, MX', 'types': [...   
56313  [{'long_name': 'Del Rio, TX, US', 'types': ['l...   
56319  [{'long_name': 'Los Garza, MX', 'types': ['loc...   
56320  [{'long_name': 'Spain', 'types': ['country', '...   
56324  [{'long_name': 'Cuautitlán, MX', 'types': ['lo...   
56325  [{'long_name': 'Ciudad Juárez, MX', 'types': [...   
56326  [{'long_name': 'Ciudad Juárez, MX', 'types': [...   
56332  [{'long_name': 'Garza García, MX', 'types': ['...   
56333  [{'long_name': 'Ciudad Juárez, MX', 'types': [...   
56335  [{'long_name': 'Cuautitlán, MX', 'types': ['lo...   
56336  [{'long_name': 'Ciudad Juárez, MX', 'types': [...   
56339  [{'long_name': 'Ecatepec, MX', 'types': ['loca...   
56340  [{'long_name': 'La Quebrada, MX', 'types': ['l...   
56342  [{'long_name': None, 'types': ['country', 'pol...   
56343  [{'long_name': 'Col', 'types': ['administrativ...   
56345  [{'long_name': 'Morelia, MX', 'types': ['local...   
56347  [{'long_name': 'Cancún, MX', 'types': ['locali...   
56348  [{'long_name': 'Ciudad Juárez, MX', 'types': [...   
56351  [{'long_name': 'Tepehua, MX', 'types': ['local...   
56352  [{'long_name': 'Estado de Hidalgo, MX', 'types...   
56353  [{'long_name': 'Juan', 'types': ['locality', '...   
56357  [{'long_name': 'Az', 'types': ['administrative...   
56358  [{'long_name': 'Ciudad Juárez, MX', 'types': [...   
56360  [{'long_name': 'Estado de Hidalgo, MX', 'types...   
56362  [{'long_name': 'Ecatepec, MX', 'types': ['loca...   

       geometry.location.lat  geometry.location.lng geometry.location_type  \
0                  31.733330            -106.483330            APPROXIMATE   
1                  40.506700              35.913300            APPROXIMATE   
2                  19.643880             -99.215980            APPROXIMATE   
4    